In [1]:
import requests as rq
import pandas as pd

In [2]:
import os

In [3]:
dataset = pd.read_csv("dataset.csv")

C:\Users\Ramil\AppData\Local\Temp\ipykernel_15572\1504519045.py:1: DtypeWarning: Columns (17,18,19,20,21,22,23,24,26,27,28,29,30,32,33,34,35,36,38) have mixed types. Specify dtype option on import or set low_memory=False.
  dataset = pd.read_csv("dataset.csv")


In [4]:
#dataset = None

In [5]:
""" for file in os.listdir("data"):
    if dataset is None:
        dataset = pd.read_csv(f"data/{file}")
    else:
        dataset = pd.concat([dataset, pd.read_csv(f"data/{file}")], ignore_index=True)
    print(len(dataset)) """

' for file in os.listdir("data"):\n    if dataset is None:\n        dataset = pd.read_csv(f"data/{file}")\n    else:\n        dataset = pd.concat([dataset, pd.read_csv(f"data/{file}")], ignore_index=True)\n    print(len(dataset)) '

In [6]:
total = 1815240

In [7]:
start = 0

In [8]:
if dataset is None:
    count = 100000

    metadatasList = []

    headers = {
        "Accept": "application/json"
    }

    for i in range(start, int(total/10), int(total/(count*10))):
        try:
            url = f"https://data.europa.eu/api/hub/search/search?q=&filter=dataset&includes=id,title.en,description.en,languages,modified,keywords,issued,catalog.id,catalog.title,catalog.country.id,distributions.id,distributions.format.label,distributions.format.id,distributions.license,categories.label,publisher&page={i}"
            response = rq.get(url, headers=headers)
            print(i*10, response)
            data = response.json()
            if(len(data["result"]["results"])>=1):
                metadatasList.extend(data["result"]["results"])
        except:
            print("Error while processing the index: " ,i)
        if(i%5000==0):
            dataset = pd.json_normalize(metadatasList)

            dataset["categories"].fillna("", inplace=True)

            dataset.loc[:, "category"] = dataset.loc[:, "categories"].apply(lambda x: x[0]['label']['en'] if x != '' else None)
            dataset["description.en"].fillna("")

            dataset.to_csv(f"dataset-{i}.csv")
            metadatasList = []

    dataset = pd.json_normalize(metadatasList)

    dataset["categories"].fillna("", inplace=True)

    dataset.loc[:, "category"] = dataset.loc[:, "categories"].apply(lambda x: x[0]['label']['en'] if x != '' else None)
    dataset["description.en"].fillna("")

    dataset.to_csv(f"dataset-{i}.csv")
    metadatasList = []

In [9]:
dataset.loc[:, "url"] = dataset.loc[:, "id"].apply(lambda x : f"https://data.europa.eu/data/datasets/{x}?locale=en")

In [10]:
dataset.loc[0, "url"]

'https://data.europa.eu/data/datasets/9656ab29-e3e2-3e46-826d-2387a34afea9?locale=en'

In [11]:
dataset.columns

Index(['Unnamed: 0.1', 'Unnamed: 0', 'id', 'keywords', 'distributions',
       'description.en', 'title.en', 'catalog.id', 'catalog.title.de',
       'catalog.country.id', 'issued', 'modified', 'publisher.name',
       'publisher.type', 'publisher.email', 'categories', 'publisher.homepage',
       'catalog.title.ga', 'publisher.resource', 'catalog.title.sk',
       'catalog.title.en', 'catalog.title.sv', 'catalog.title.nl',
       'catalog.title.fr', 'catalog.title.it', 'category', 'catalog.title.ro',
       'catalog.title.pt', 'catalog.title.es', 'catalog.title.fi',
       'catalog.title.lv', 'catalog.title.cs', 'catalog.title.no',
       'catalog.title.hr', 'catalog.title.sl', 'catalog.title.hu',
       'catalog.title.da', 'catalog.title.pl', 'catalog.title.et',
       'title.ennlp', 'description.ennlp', 'categorynlp', 'url'],
      dtype='object')

In [12]:
import spacy as sp

In [13]:
nlp = sp.load("en_core_web_lg")

In [14]:
dataset["description.en"].loc[0]

'Turkish nationals per 100 inhabitants (Monitoring Social Urban Development 2006)'

In [15]:
nlp(dataset["description.en"][0]).similarity(nlp(dataset["description.en"][1]))

0.6985235810279846

In [16]:
pr_count = len(dataset["description.en"])

In [17]:
import numpy as np

In [18]:
columns = ["title.en", "description.en", "category"]

In [19]:
fs = np.load("similarity.npy")

In [20]:
#fs = None

In [21]:
for column in columns:
    if not column+"nlp" in dataset.columns:
        dataset.loc[:, column+"nlp"] = dataset.loc[:, column].apply(lambda x: nlp(str(x)))

In [22]:
if fs is None:
    fs = np.array([[-1 for _ in range(pr_count)] for _ in range(pr_count)], dtype='d')
    for i in range(pr_count):
        for j in range(i+1, pr_count):
            sim = 0
            for column in columns:
                t1, t2 = dataset[column+"nlp"][i], dataset[column+"nlp"][j]
                s = 0
                if t1 and t2:
                    s = t1.similarity(t2)
                sim += s*s
            fs[i][j] = sim
            fs[j][i] = sim
        print(i)

    np.save("similarity.npy", fs)

In [23]:
threshold = 85

In [24]:
pr_count

17656

In [25]:
sample_count = pr_count
sample = []
for i in range(0, pr_count, int(pr_count/sample_count)):
    main_dataset = dataset.loc[i]
    recommended_datasets = dataset.loc[np.nonzero(fs[i]>threshold*3/100)].to_dict('records')
    sample.append((main_dataset, recommended_datasets))

In [26]:
set([x[0]["category"] for x in sample])

{'Agriculture, fisheries, forestry and food',
 'Economy and finance',
 'Education, culture and sport',
 'Energy',
 'Environment',
 'Government and public sector',
 'Health',
 'International issues',
 'Justice, legal system and public safety',
 'Population and society',
 'Provisional data',
 'Regions and cities',
 'Science and technology',
 'Transport',
 nan}

In [27]:
survey_sample = [(x[0], x[1][:5]) for x in filter(lambda x: len(x[1])>5 and not pd.isna(x[0]["category"]) and not pd.isna(x[0]["description.en"]), sample)]

In [87]:
d = dict()

In [88]:
for x in survey_sample:
    c = x[0]["category"]
    if c in d:
        d[c].append(x)
    else:
        d[c] = [x]

In [89]:
d.keys()

dict_keys(['Government and public sector', 'Regions and cities', 'Environment', 'Justice, legal system and public safety', 'Economy and finance', 'Transport', 'Education, culture and sport', 'Population and society', 'Agriculture, fisheries, forestry and food', 'Science and technology', 'Health', 'Energy', 'Provisional data'])

In [90]:
set([x[0]["category"] for x in survey_sample])

{'Agriculture, fisheries, forestry and food',
 'Economy and finance',
 'Education, culture and sport',
 'Energy',
 'Environment',
 'Government and public sector',
 'Health',
 'Justice, legal system and public safety',
 'Population and society',
 'Provisional data',
 'Regions and cities',
 'Science and technology',
 'Transport'}

In [91]:
survey_count = 20

In [92]:
survey = []

In [93]:
for key in d.keys():
    survey.append(d[key][0])

In [94]:
for key in d.keys():
    if(len(d[key])>1):
        survey.append(d[key][1])

In [95]:
for key in d.keys():
    if(len(d[key])>2):
        survey.append(d[key][2])

In [96]:
survey.pop(15)
survey.pop(15)
survey.pop(15)
survey.pop(15)
survey.pop(4)
survey.pop(19)
survey.pop(19)
survey.pop(19)

(Unnamed: 0.1                                                         60
 Unnamed: 0                                                       6000.0
 id                                             cz-cuzk-zm10-rb-09440722
 keywords                                                            NaN
 distributions                                                       NaN
 description.en        Since 2001, the ZM 10 is produced using digita...
 title.en              Base map CR 1:10,000 - colour seamless - 09440722
 catalog.id                                                         cuzk
 catalog.title.de                                                    NaN
 catalog.country.id                                                   cz
 issued                                                              NaN
 modified                                                            NaN
 publisher.name                                                      NaN
 publisher.type                                    

In [97]:
#survey = [survey_sample[i] for i in range(0, len(survey_sample), int(len(survey_sample)/survey_count))]

In [98]:
#survey = survey[1:-1:2]

In [99]:
survey = survey[:survey_count]

In [100]:
len(survey)

20

In [101]:
dataset.loc[np.nonzero(fs[1]*fs[1]>threshold*3/100)].to_dict('records')

[{'Unnamed: 0.1': 2,
  'Unnamed: 0': 200.0,
  'id': 'b4f14366-ef3e-497a-ab2b-811174135f0c',
  'keywords': "[{'language': 'ga', 'id': 'nqq03', 'label': 'NQQ03'}, {'language': 'ga', 'id': 'cso', 'label': 'cso'}, {'language': 'ga', 'id': 'national-accounts', 'label': 'national-accounts'}]",
  'distributions': "[{'format': {'id': 'PX', 'label': 'PX'}, 'id': '8d8ad5b3-0765-4425-8719-12acfd041224'}, {'format': {'id': 'JSON-STAT', 'label': 'JSON-STAT'}, 'id': 'b92a0dbb-a937-4304-a0b9-6a9061b70f5c'}, {'format': {'id': 'XLSX', 'label': 'XLSX'}, 'id': '85817193-a7e9-4ab2-9f75-861455492117'}, {'format': {'id': 'CSV', 'label': 'CSV'}, 'id': 'a7f17502-9b8b-4ba3-923b-130091926278'}]",
  'description.en': 'Expenditure on Gross National Product (chain linked annually referenced to 2005)',
  'title.en': 'NQQ03 — Expenditure on Gross National Product (chain linked annually referenced to 2005)',
  'catalog.id': 'data-gov-ie',
  'catalog.title.de': nan,
  'catalog.country.id': 'ie',
  'issued': '2021-07-0

In [237]:
import jinja2 as jj

In [238]:
fsl = jj.FileSystemLoader(searchpath="templates")

In [239]:
env = jj.Environment(loader=fsl)

In [240]:
fsl.list_templates()

['template.jinja']

In [241]:
template = env.get_template("template.jinja")

In [242]:
recs = []

In [243]:
survey[0][0]["description.en"]

'The service includes all development plans and statutes of the municipality of Marienheide. It should be noted that the overview is not exhaustive. If you have any questions about a development plan and its stipulations or statutes, please contact us. (planung@marienheide.de)'

In [244]:
indexHtml = template.render(survey = survey, count=len(survey)).encode( "utf-8" )

In [245]:
file=open("index.html", "wb")
file.write(indexHtml)
file.close()

In [246]:
survey[2][0]["title.en"]

'As DSM CRS3035RES50000mN2700000E4250000 elevation grid 1\xa0m cut-off date 15.9.2019'

In [247]:
survey[2][1][0]["title.en"]

'AS DTM CRS3035RES50000mN2700000E4450000 Height grid 1m Deadline 15.09.2023'

In [233]:
medians = [np.median(fs[i]) for i in range(len(fs))]

In [234]:
medians

[np.float64(0.7223111376855106),
 np.float64(1.295244046079198),
 np.float64(1.1137841985831662),
 np.float64(0.9753099463619027),
 np.float64(0.7436195886010737),
 np.float64(1.076354379786827),
 np.float64(0.7623102339681153),
 np.float64(1.164897954143943),
 np.float64(1.0772543996330872),
 np.float64(0.4428268129284706),
 np.float64(0.12813918263987112),
 np.float64(1.0273354454089834),
 np.float64(0.9802131374803826),
 np.float64(0.1595470517022191),
 np.float64(0.31447155983904507),
 np.float64(1.0403868094259),
 np.float64(0.13363961614374453),
 np.float64(1.026208313796131),
 np.float64(1.0108810676062046),
 np.float64(1.2178066236902447),
 np.float64(1.0306947411500609),
 np.float64(1.1710065487362884),
 np.float64(1.135198368001014),
 np.float64(1.1922874217113093),
 np.float64(1.079410012424034),
 np.float64(1.2211253543107161),
 np.float64(1.2570753001984438),
 np.float64(1.1567306285907952),
 np.float64(0.9502400354581728),
 np.float64(0.337699751138421),
 np.float64(0.945

In [235]:
np.median(medians)*2/3

np.float64(0.6874422316874584)

In [236]:
dataset.loc[4999, "title.en"]

'Building Plans Merzig/Schwemlingen — In der Schank'